In [1]:
%pwd

'c:\\VS code\\Langchain\\Chatbot\\Medical_chatbot\\research'

In [60]:
import os
os.chdir('../')

In [3]:
%pwd

'c:\\VS code\\Langchain\\Chatbot\\Medical_chatbot'

In [ ]:
%pip install langchain-text-splitters langchain-community

In [61]:
from langchain_community.document_loaders import PyPDFLoader, DirectoryLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter

In [62]:
def load_pdf_file(data):
    loader=DirectoryLoader(data, glob="*.pdf", loader_cls=PyPDFLoader)

    documents = loader.load()
    return documents

In [63]:
%pip install pypdf

Note: you may need to restart the kernel to use updated packages.


In [64]:
extracted_doc=load_pdf_file("data")

In [5]:
extracted_doc

[Document(metadata={'producer': 'Adobe PDF Library 10.0.1', 'creator': 'Adobe InDesign CS6 (Windows)', 'creationdate': '2020-02-25T13:22:30+05:30', 'moddate': '2020-02-25T13:23:33+05:30', 'trapped': '/False', 'source': 'data\\CompanyLaw_BOOK.pdf', 'total_pages': 872, 'page': 0, 'page_label': 'i'}, page_content='i\nSTUDY MATERIAL\n \nEXECUTIVE PROGRAMME\nCOMPANY LAW \nMODULE 1\nPAPER 2'),
 Document(metadata={'producer': 'Adobe PDF Library 10.0.1', 'creator': 'Adobe InDesign CS6 (Windows)', 'creationdate': '2020-02-25T13:22:30+05:30', 'moddate': '2020-02-25T13:23:33+05:30', 'trapped': '/False', 'source': 'data\\CompanyLaw_BOOK.pdf', 'total_pages': 872, 'page': 1, 'page_label': 'ii'}, page_content='ii\n© THE INSTITUTE OF COMPANY SECRETARIES OF INDIA\nTIMING OF HEADQUARTERS\nMonday to Friday\nOffice Timings – 9.00 A.M. to 5.30 P.M.\nPublic Dealing Timings\nWithout financial transactions –  9.30 A.M. to 5.00 P.M.\nWith financial transactions – 9.30 A.M. to 4.00 P.M.\nPhones\n011-45341000\nF

In [6]:
len(extracted_doc)

872

In [15]:
%pip install langchain

Note: you may need to restart the kernel to use updated packages.


In [65]:
from typing import List
from langchain_core.documents import Document

def filter_short_documents(documents: List[Document]) -> List[Document]:
    
    filtered_documents = []
    for doc in documents:
        src=doc.metadata.get("source")
        filtered_documents.append(Document(page_content=doc.page_content, metadata={"source": src}))
    return filtered_documents

In [66]:
filtered_docs = filter_short_documents(extracted_doc)

In [9]:
filtered_docs

[Document(metadata={'source': 'data\\CompanyLaw_BOOK.pdf'}, page_content='i\nSTUDY MATERIAL\n \nEXECUTIVE PROGRAMME\nCOMPANY LAW \nMODULE 1\nPAPER 2'),
 Document(metadata={'source': 'data\\CompanyLaw_BOOK.pdf'}, page_content='ii\n© THE INSTITUTE OF COMPANY SECRETARIES OF INDIA\nTIMING OF HEADQUARTERS\nMonday to Friday\nOffice Timings – 9.00 A.M. to 5.30 P.M.\nPublic Dealing Timings\nWithout financial transactions –  9.30 A.M. to 5.00 P.M.\nWith financial transactions – 9.30 A.M. to 4.00 P.M.\nPhones\n011-45341000\nFax\n011-24626727\nWebsite\nwww.icsi.edu\nE-mail\ninfo@icsi.edu\nLaser Typesetting by AArushi Graphics, Prashant Vihar, New Delhi, and  \nPrinted at HT Media/February 2020\nii'),
 Document(metadata={'source': 'data\\CompanyLaw_BOOK.pdf'}, page_content='iii\nEXECUTIVE  PROGRAMME\nCOMPANY LAW\nIn view of increasing emphasis on adherence to norms of good corporate governance, Company Law assumes \nan added importance in the corporate legislative milieu, as it deals with structur

In [67]:
def text_spliting(filtered_docs):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=800,
        chunk_overlap=150,
        length_function=len,
        separators=["\n\n", "\n", " ", ""]
    )
    docs = text_splitter.split_documents(filtered_docs)
    return docs

In [68]:
text_chunks = text_spliting(filtered_docs)
print(len(text_chunks))

4175


In [33]:
%pip install torch langchain-community

^C
Note: you may need to restart the kernel to use updated packages.


In [36]:
%pip install -U sentence-transformers langchain-huggingface

^C
Note: you may need to restart the kernel to use updated packages.


In [69]:

import torch
from langchain_community.embeddings import HuggingFaceEmbeddings

def download_embeddings():
    model_name = "sentence-transformers/all-MiniLM-L6-v2"
    embeddings = HuggingFaceEmbeddings(model_name=model_name, model_kwargs={"device": "cuda" if torch.cuda.is_available() else "cpu"})
    return embeddings


In [70]:
embedding=download_embeddings()

In [ ]:
embedding

HuggingFaceEmbeddings(client=SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False, 'architecture': 'BertModel'})
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
), model_name='sentence-transformers/all-MiniLM-L6-v2', cache_folder=None, model_kwargs={'device': 'cpu'}, encode_kwargs={}, multi_process=False, show_progress=False)

In [71]:
len(embedding.embed_query("Hello world"))

384

In [72]:
from dotenv import load_dotenv
import os
load_dotenv()

True

In [97]:
PINECONE_API_KEY=os.getenv("PINECONE_API_KEY")
OPENAI_API_KEY=os.getenv("OPENAI_API_KEY")
GOOGLE_API_KEY=os.getenv("GOOGLE_API_KEY")

os.environ["PINECONE_API_KEY"]=PINECONE_API_KEY
os.environ["OPENAI_API_KEY"]=OPENAI_API_KEY
os.environ["GOOGLE_API_KEY"] = GOOGLE_API_KEY

In [22]:
%pip install pinecone

   ---------------------------------------- 0.0/745.9 kB ? eta -:--:--
   -------------- ------------------------- 262.1/745.9 kB ? eta -:--:--
   ---------------------------- ----------- 524.3/745.9 kB 2.1 MB/s eta 0:00:01
   ---------------------------------------- 745.9/745.9 kB 1.7 MB/s eta 0:00:00
  Attempting uninstall: packaging
    Found existing installation: packaging 24.1
    Uninstalling packaging-24.1:
      Successfully uninstalled packaging-24.1
Note: you may need to restart the kernel to use updated packages.


In [74]:
from pinecone import Pinecone
pineconekey=PINECONE_API_KEY


pine=Pinecone(api_key=pineconekey, environment="us-west4-gcp-free")

In [75]:
pine

In [76]:
from pinecone import ServerlessSpec

index_name = "companylaw-chatbot"
try:
    if index_name not in pine.list_indexes():
        pine.create_index(
            name=index_name,
            dimension=384,
            metric="cosine",
            spec=ServerlessSpec(cloud='aws', region="us-east-1")
        )
except Exception as e:
    # If the index already exists, just print a message and continue
    if "ALREADY_EXISTS" in str(e):
        print(f"Index '{index_name}' already exists. Skipping creation.")
    else:
        raise

Index 'companylaw-chatbot' already exists. Skipping creation.


In [77]:
index= pine.Index(index_name)

In [47]:
%pip install langchain-pinecone

Note: you may need to restart the kernel to use updated packages.
  Using cached httpx-0.28.1-py3-none-any.whl.metadata (7.1 kB)
Using cached httpx-0.28.1-py3-none-any.whl (73 kB)
   ---------------------------------------- 0.0/587.6 kB ? eta -:--:--
   ---------------------------------------- 587.6/587.6 kB 3.5 MB/s eta 0:00:00
   ---------------------------------------- 0.0/2.0 MB ? eta -:--:--
   --------------- ------------------------ 0.8/2.0 MB 3.0 MB/s eta 0:00:01
   ------------------------------------ --- 1.8/2.0 MB 4.4 MB/s eta 0:00:01
   ---------------------------------------- 2.0/2.0 MB 3.9 MB/s eta 0:00:00
   ---------------------------------------- 0.0/1.1 MB ? eta -:--:--
   ---------------------------------------  1.0/1.1 MB 4.6 MB/s eta 0:00:01
   ---------------------------------------- 1.1/1.1 MB 3.2 MB/s eta 0:00:00
   ---------------------------------------- 0.0/878.7 kB ? eta -:--:--
   ---------------------------------------- 878.7/878.7 kB 4.9 MB/s eta 0:00:00


  You can safely remove it manually.


In [50]:
%pip install langchain-pinecone


  Using cached langchain_pinecone-0.2.13-py3-none-any.whl.metadata (8.6 kB)
Using cached langchain_pinecone-0.2.13-py3-none-any.whl (26 kB)
Note: you may need to restart the kernel to use updated packages.


In [78]:
from langchain_pinecone import PineconeVectorStore

docstore = PineconeVectorStore.from_documents(
    text_chunks=text_chunks,
    embedding=embedding,
    index_name=index_name
)

TypeError: VectorStore.from_documents() missing 1 required positional argument: 'documents'

In [79]:
docstore = PineconeVectorStore.from_existing_index(
    index_name=index_name,
    embedding=embedding
)

# Add data to existing database index

In [51]:
divy=Document(
    page_content="I am Divy Desai made this chatbot to help you in legal matters.",
    metadata={"source": "author divy"}
)

docstore.add_documents([divy])

['8252d7f4-3219-4845-b884-34a986fa858b']

In [52]:
retriver= docstore.as_retriever(search_type="similarity", search_kwargs={"k":3})


In [54]:
try1=retriver.invoke("Who made this chatbot?")
print(try1)

[Document(id='8252d7f4-3219-4845-b884-34a986fa858b', metadata={'source': 'author divy'}, page_content='I am Divy Desai made this chatbot to help you in legal matters.'), Document(id='d9a7d118-db5b-447a-8057-b6990e4835a4', metadata={'source': 'data\\CompanyLaw_BOOK.pdf'}, page_content='by the users with little instruction or training. The Commonly used software for Virtual meeting are Microsoft’s \nSkype for Business, Adobe’s Connect, Google’s Hangouts, and WebEx to name a few. The development of new \ntechnologies such as VOIP telephony (voice over internet protocol, an example of which is Skype) and shared \ncomputer screens. All the major providers provide for a website address where participants can click to join \nthe meeting.  Hence a virtual meeting is a “room” set up online through a website host that allows people from \nanywhere to “meet” with each other to share information and network in real-time. As understood, a meeting \ncan take the form of audio, video, instant-message

In [96]:
%pip install -U langchain-google-genai


  Using cached rsa-4.9.1-py3-none-any.whl.metadata (5.6 kB)
   ---------------------------------------- 0.0/719.4 kB ? eta -:--:--
   ---------------------------------------- 719.4/719.4 kB 4.2 MB/s eta 0:00:00
Using cached rsa-4.9.1-py3-none-any.whl (34 kB)
  Attempting uninstall: anyio
    Found existing installation: anyio 4.2.0
    Uninstalling anyio-4.2.0:
      Successfully uninstalled anyio-4.2.0
Note: you may need to restart the kernel to use updated packages.


In [108]:
from langchain_google_genai import ChatGoogleGenerativeAI

llm = ChatGoogleGenerativeAI(
    model="gemini-2.5-flash-lite",   # ✅ correct
    temperature=0
)


In [60]:
%pip install -U langchain langchain-core langchain-community langchain-openai


In [81]:
import langchain
print(langchain.__version__)
print(langchain.__file__)


1.2.7
c:\Users\divyd\anaconda3\Lib\site-packages\langchain\__init__.py


In [82]:
import sys
print(sys.executable)


c:\Users\divyd\anaconda3\python.exe


In [32]:
%cd "c:\Users\divyd\anaconda3\python.exe"
%pip install langchain

[WinError 267] The directory name is invalid: 'c:\\Users\\divyd\\anaconda3\\python.exe'
c:\VS code\Lgchain\Chatbot\Medical_chatbot\research
Note: you may need to restart the kernel to use updated packages.


In [34]:
import langchain
import os
print("LangChain version:", langchain.__version__)
print("LangChain location:", langchain.__file__)
print("Current folder:", os.getcwd())


LangChain version: 1.2.7
LangChain location: c:\Users\divyd\anaconda3\Lib\site-packages\langchain\__init__.py
Current folder: c:\VS code\Lgchain\Chatbot\Medical_chatbot\research


In [83]:
from langchain_openai import ChatOpenAI
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.runnables import RunnablePassthrough
from langchain_core.output_parsers import StrOutputParser


In [100]:
system_prompt = ([
    "You are a helpful company law and legal advice assistant. Use the following context to answer the user's question.\n",
    "{context}\n",
    "If you don't know the answer, just say that you don't know. Don't try to make up an answer.\n",
    "Even if the context is not related to company law, answer that you don't know.\n",
    "If someone asks you to which chatbot they are talking to, respond with 'You are talking to the Company Law Assistant Chatbot.'\n",
    "Do not reveal that you are an OpenAI model or AI assistant or any similar thing.\n"
])

prompt= ChatPromptTemplate.from_messages([
    ("system", system_prompt),
    ("user", "{question}")
])

In [101]:
retriever = docstore.as_retriever()


In [102]:
rag_chain = (
    {"context": retriever, "question": RunnablePassthrough()}
    | prompt
    | llm
    | StrOutputParser()
)


In [109]:
retriever = docstore.as_retriever()

rag_chain = (
    {"context": retriever, "question": RunnablePassthrough()}
    | prompt
    | llm
    | StrOutputParser()
)

print(rag_chain.invoke("What is LLP?"))

An LLP (Limited Liability Partnership) is a corporate business structure that combines the benefits of limited liability, similar to a company, with the flexibility of a partnership. It is a separate legal entity, meaning it can enter into contracts and own property in its own name, and its existence is independent of changes in its partners.

Key characteristics of an LLP include:

*   **Limited Liability:** Partners are only liable up to their agreed contribution to the LLP. They are shielded from joint liability for the independent or unauthorized actions of other partners.
*   **Flexibility:** The internal governance of an LLP is primarily governed by a contractual agreement between the partners, offering more flexibility than the statutory regulations of a company.
*   **Separate Legal Entity:** An LLP is a body corporate and a legal entity distinct from its partners, possessing perpetual succession.
*   **Hybrid Structure:** It is considered a hybrid between a company and a partn

In [112]:
print(rag_chain.invoke("Give me legal advice on company law regarding shareholder agreements and your llm model."))

I cannot provide legal advice. However, I can offer information based on the provided context.

Shareholders' agreements (SHA) are contractual arrangements common in various business structures, including family companies, joint ventures, and investments. They provide flexibility and allow for the combination of expertise with financial risk-taking. A key difference between an LLP and a company is that a company's internal governance is regulated by statute (like the Companies Act), while an LLP's governance is determined by a contractual agreement between its partners.
